In [1]:
import pyLPM
import pandas as pd
import RBFN
import numpy as np
from sklearn.preprocessing import MinMaxScaler

In [2]:
walter = pd.read_csv('data/walker.csv')

In [3]:
walter.drop(columns=['Id','U','T'], inplace=True)

In [4]:
walter.head()

X     Y      V
0  11.0   8.0    0.0
1   8.0  30.0    0.0
2   9.0  48.0  224.4
3   8.0  69.0  434.4
4   9.0  90.0  412.1

In [5]:
walter['Z'] = np.zeros(len(walter))

In [6]:
#walter.V=(walter.V-walter.V.min())/(walter.V.max()-walter.V.min())

In [7]:
walter.head()

X     Y      V    Z
0  11.0   8.0    0.0  0.0
1   8.0  30.0    0.0  0.0
2   9.0  48.0  224.4  0.0
3   8.0  69.0  434.4  0.0
4   9.0  90.0  412.1  0.0

In [8]:
coordinates = walter[['X','Y','Z']]

In [9]:
RBFN.cluster_centers_evaluation(coordinates=coordinates, 
                                max_num_clusters=40)

In [10]:
n_clus = 200

In [11]:
centers = RBFN.cluster_centers(n_clus=n_clus,
                               coordinates=coordinates)

In [12]:
rbf_n = RBFN.RBFN(cluster_centers=centers, 
          sigma=None)

In [13]:
rbf_n.knn_sigma_definition(neighbors_number=5)

In [14]:
rbf_n.random_bias()

Random bias: 0.41048331605964195


In [15]:
rbf_n.fit(X=coordinates.values, 
          y=walter.V.values)

In [16]:
grid = pyLPM.utils.autogrid(x=walter.X, y=walter.Y, z=walter.Z, sx=5, sy=5, sz=1)

In [17]:
X = pyLPM.utils.add_coord(grid)

In [18]:
predict = rbf_n.predict(X)

In [19]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict,
    categorical=False,
    points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [20]:
X_train, X_test, y_train, y_test = RBFN.train_test_sets_builder(walter, 'X', 'Y', 'Z', 'V')

In [21]:
rbf_n.train(4000, X_train, X_test, y_train, y_test, learning_rate_w=0.00001)

In [22]:
predict_train = rbf_n.predict(X)

In [23]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict_train,
    categorical=False,
    points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [24]:
rbf_n.weights = np.random.randn(n_clus+1)

In [25]:
predict_random_weights = rbf_n.predict(X)

In [26]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict_random_weights,
    categorical=False,
    points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [27]:
rbf_n.train(10000, X_train, X_test, y_train, y_test, learning_rate_w=0.0006)

In [28]:
predict_trained_weights = rbf_n.predict(X)

In [29]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict_trained_weights,
    categorical=False,
    points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)